In [ ]:
import bpy
from IPython.display import display
from anywidget_3dviewer import Viewer
import solara
from pathlib import Path


def make_gltf_model():
    bpy.ops.preferences.addon_enable(module="io_scene_gltf2")
    bpy.ops.object.select_all(action="DESELECT")
    bpy.ops.object.select_by_type(type="MESH")

    bpy.ops.object.delete()
    bpy.ops.mesh.primitive_cube_add(size=2, align="WORLD", location=(0, 1, 1))
    cube = bpy.context.active_object
    gltf_path = "./model_cube.gltf"
    bpy.ops.object.select_all(action="DESELECT")
    cube.select_set(True)
    bpy.ops.export_scene.gltf(
        filepath=gltf_path, export_format="GLTF_EMBEDDED", use_selection=True
    )
    gltf_path = Path() / "model_cube.gltf"
    data = gltf_path.read_bytes()
    gltf_path.unlink()
    return data


data = make_gltf_model()
    

do_render = solara.reactive(False)

data = make_gltf_model()

@solara.component
def Page():

    def render():
        if do_render.value:
            return data
   
    result = solara.use_thread(render, [do_render.value])
    if not do_render.value:
        solara.Button("Start Rendering", on_click=lambda: do_render.set(True), color="orange")
    else:
        if result.state == solara.ResultState.RUNNING:
            solara.Info("Rendering in progress...")
            solara.ProgressLinear()
        elif result.state == solara.ResultState.ERROR:
            solara.Error("Rendering failed!: %s" % result.error)
        elif result.state == solara.ResultState.FINISHED:
            with solara.Column():
                solara.Success("Rendering complete. ")
                if result.value:
                    viewer = Viewer(gltf_data=result.value)
                    solara.FileDownload(data, filename="model_cube.gltf", label="Download model_cube.gltf")

                    display(viewer)
Page()